## I. Importing data

In [14]:
import pandas as pd
import numpy as np
data_x = pd.read_csv('traininginputs.csv')
data_y = pd.read_csv('trainingoutput.csv')

## II. Cleaning data 

In [15]:
data = pd.merge(data_x, data_y, on='PROC_TRACEINFO', how ='inner')

Nous explorant notre base de donnée afin de se faire une idée sur son contenu. Pour cela commencons par voir les dimensions de notre dataset (nombre d'observations et de variables):

In [16]:
nbr_lignes, nbr_colonnes = data.shape
print("Nbr de lignes :", nbr_lignes )
print("Nbr de colonnes :",nbr_colonnes )

Nbr de lignes : 34515
Nbr de colonnes : 15


Nous avons donc 14 variables pour 34.515 individus. 

Vérifions s'il y a des valeurs manquantes.

In [17]:
data.isna().sum()

PROC_TRACEINFO                         0
OP070_V_1_angle_value                  0
OP090_SnapRingPeakForce_value          0
OP070_V_2_angle_value                  0
OP120_Rodage_I_mesure_value            0
OP090_SnapRingFinalStroke_value        0
OP110_Vissage_M8_torque_value          0
OP100_Capuchon_insertion_mesure    18627
OP120_Rodage_U_mesure_value            0
OP070_V_1_torque_value                 0
OP090_StartLinePeakForce_value         0
OP110_Vissage_M8_angle_value           0
OP090_SnapRingMidPointForce_val        0
OP070_V_2_torque_value                 0
Binar OP130_Resultat_Global_v          0
dtype: int64

Il semblerait que la variable 'OP100_Capuchon_insertion_mesure' compte 18.627 valeurs manquantes soit pour 53% des observations. Dans ce cas il serait difficile et pas pertinant de remplacer ces valeurs manquantes. Deux options s'offrirons a nous : utiliser des modèles qui gèrent les valeurs manquantes ou tout simplement supprimer cette variable. Les deux options seront explorées.

In [18]:
type_col = data.dtypes
print(type_col)

PROC_TRACEINFO                      object
OP070_V_1_angle_value              float64
OP090_SnapRingPeakForce_value      float64
OP070_V_2_angle_value              float64
OP120_Rodage_I_mesure_value        float64
OP090_SnapRingFinalStroke_value    float64
OP110_Vissage_M8_torque_value      float64
OP100_Capuchon_insertion_mesure    float64
OP120_Rodage_U_mesure_value        float64
OP070_V_1_torque_value             float64
OP090_StartLinePeakForce_value     float64
OP110_Vissage_M8_angle_value       float64
OP090_SnapRingMidPointForce_val    float64
OP070_V_2_torque_value             float64
Binar OP130_Resultat_Global_v        int64
dtype: object


La variable PROC_TRACEINFO est sous format 'object' et n a aucun interet. L énnoncé confirme qu il s agit Id de pieces. Nous décidons donc de la supprimer:

In [19]:
data = data.drop('PROC_TRACEINFO', axis =1 )

OK toutes les variables sont quantitatives. 
Par contre notre prédicteur (Binar OP130_Resultat_Global_v) devrait etre une variable catégorielle a deux modalités et non une variable continue. Nous procédons donc au changement de son type.

In [20]:
data['Binar OP130_Resultat_Global_v'] = data['Binar OP130_Resultat_Global_v'].astype('category')
print(data['Binar OP130_Resultat_Global_v'].dtype)

category


## III. Data analysis 

L'analyse de donnée est un travail déterminant pour la bonne compréhension de nos données et permet parfois de mieux aiguiller le travail de modélisation. L'analyse de données permet d'étudier aussi bien la relation entre les différentes variables mais aussi de se faire une idée sur la population (exemple son homogénéité). Dans le cas ou l'on a une population hétérogène, il serait pertinant de créer plusieurs groupes d'observations, dans ce cas deux solutions sont envisageables : développer un modèle par groupe homoène d'invidus , ou encore rajouter une variable dans notre base de donnée qui porterait le groupe auquel appartiendrait chaque observation. L'inconvénient de cette stratégie est que pour chaque nouvelle observation , il faudra tout d'abord déterminer le groupe auquel elle appartient avant de l'intégrer dans le modèle.

In [21]:
print(data.describe())

       OP070_V_1_angle_value  OP090_SnapRingPeakForce_value   
count           34515.000000                   34515.000000  \
mean              159.906922                     156.915055   
std                15.662650                      11.271492   
min               101.800000                       0.000000   
25%               148.700000                     149.210000   
50%               158.000000                     156.180000   
75%               169.300000                     164.380000   
max               198.300000                     196.920000   

       OP070_V_2_angle_value  OP120_Rodage_I_mesure_value   
count           34515.000000                 34515.000000  \
mean              159.618236                   113.350222   
std                15.091490                     3.528522   
min                82.000000                    99.990000   
25%               149.400000                   111.040000   
50%               158.700000                   113.160000   
75%  

Contenu de la présence de valeurs manquantes dans l une de nos varibles nous décidons de partir un XGboost directement en premier essai car il intégre la possibilité de gestion de valeurs manquantes.

# IV. Machine learning modeling

#### Diviser les données en train/test et définition des paramètres de la Validation croisée:

In [22]:
import xgboost as xgb
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.metrics import make_scorer, roc_auc_score

Séparer les données en prédicteur (y) / variables prédictives (X) :

In [23]:
y = data['Binar OP130_Resultat_Global_v']
X = data.drop('Binar OP130_Resultat_Global_v', axis =1)

Nous séparons notre dataset en train/test en choisissant d'allouer 20% aux données test.  

In [24]:
X_train, X_test, y_train, y_test= train_test_split(X, y,test_size=0.2, random_state=123)

### Option 1 : modélisation avec XG Boost:

In [25]:
# définition du modèle xgboost
model = xgb.XGBClassifier()

XGBoost, en tant qu'algorithme de boosting basé sur des arbres de décision, n'a  pas besoin de centrer ou de réduire les données en amont. Nous procédons donc au paramètrage de notre modèle. 

Comme évoqué précédemment, XGBoost est capable de gérer les valeurs manquantes automatiquement. Aucune configuration ne sera donc necessaire pour la gestion des valeurs manquantes.

#### 1.1 Recherche de paramètres : selection manuelle des hyperparamètres

Deux types de paramètres: 
paramètres intervenant lors du calcul du gain /interet d ajouter un nouvel étage et donc structure de l arbre  & 
paramètres lors du calcul du poids optimal a chaque feuille d abre, impact au niveau l impact donc prédiction faite:

In [26]:


# Spécifiez la grille des hyperparamètres à explorer
param_grid = {
    'learning_rate': [0.04, 0.05 ,0.06], # fraction de la correction appliquée
    'n_estimators': [50, 100, 200], # nombre d arbres a entrainer séquentiellement pour faire prédicteur final (biais /variance)
    'max_depth': [3, 4, 5,6], #profondeur maximale de ce que peut atteindre un arbre et donc des valeurs qu'il peut prendre soit 2^max_depth
    'min_child_weight': [1, 2, 3],
    'gamma': [0.05, 0.1, 0.2], #définit le seuil du gain qu'apporte l'ajou de chaque nouveau noeud (0 -> pas de seuil)
    'subsample': [0.8, 0.9, 1.0],
    'colsample_bytree': [0.8, 0.9, 0.7],
}

# Créez un objet GridSearchCV pour la recherche par grille
grid_search = GridSearchCV(model, param_grid, scoring='roc_auc', cv=5, verbose=10, n_jobs=-1)

# Entraînez le modèle en utilisant la recherche par grille
grid_search.fit(X_train, y_train)

# Affichez les meilleurs hyperparamètres trouvés
print("Meilleurs hyperparamètres:", grid_search.best_params_)


Fitting 5 folds for each of 4860 candidates, totalling 24300 fits


[CV 1/5; 1/4860] START colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.8
[CV 3/5; 1/4860] START colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.8
[CV 5/5; 1/4860] START colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.8
[CV 4/5; 1/4860] START colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.8
[CV 2/5; 1/4860] START colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.8
[CV 2/5; 2/4860] START colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.9
[CV 1/5; 1/4860] END colsample_bytree=0.8, gamma=0.05, learning_rate=0.01, max_depth=3, min_child_weight=1, n_estimators=50, subsample=0.8;, score=0.631 t

In [27]:
best_params = grid_search.best_params_ #enregistre les meilleurs paramètres trouvés.

best_model = xgb.XGBClassifier(**best_params)  # Remplacez XGBClassifier par le modèle que vous utilisez

best_model.fit(X_train, y_train) #entrainer le modèle avec les meilleurs paramètres trouvés.

y_pred_proba = best_model.predict_proba(X_test)[:, 1]  # prédire sur la partie X_test par vos données de test

roc_auc = roc_auc_score(y_test, y_pred_proba)  # Remplacez y_test par vos étiquettes de test

print("ROC AUC Score:", roc_auc)

ROC AUC Score: 0.7066849126907246


Avec cette approche nous arrivons au score 0.70 ROC_AUC ce qui est suppérieur au score de 0.675 obtenu par Valéo en utilisant une   classification naïve bayésienne. 

Pour l'obtention de ce score, les meilleurs hyperparamètres sont :  {'colsample_bytree': 0.8, 'gamma': 0.1, 'learning_rate': 0.06, 'max_depth': 4, 'min_child_weight': 1, 'n_estimators': 100, 'subsample': 1.0}

Néanmoins, l'inconvénient de l'approche 'brute force' est cette méthode soit biaisée par l'invention de l'humain. Le champs des paramètres possibles étant très large , le risque de tomber sur un 'minimal local' est aggravé par les limites de notre capacité calulatoire.

#### 1.2 Recherche de paramètres : approche 'Halving Grid search'.

Chercher des paramètres sur des échantillons de plus en plus important en écartant a chaque itération la moitiée des combinaisons les moins performantes.

#### 1.3 Recherche de paramètres : approche 'pure random'

Permet d'explorer le champs des possibles sans forcément trouver la combinaison optimale. L'avantage que présente cette méthode est de pouvoir maitriser le temps de calcul.

#### 1.4 Recherche de paramètres : approche 'substitut'

In [34]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from skopt import BayesSearchCV

In [39]:
pip install --upgrade numpy


  Obtaining dependency information for numpy from https://files.pythonhosted.org/packages/35/21/9e150d654da358beb29fe216f339dc17f2b2ac13fff2a89669401a910550/numpy-1.26.0-cp311-cp311-macosx_11_0_arm64.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.7/99.7 kB 5.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.0/14.0 MB 24.6 MB/s eta 0:00:0000:0100:01
  Attempting uninstall: numpy
    Found existing installation: numpy 1.24.2
    Uninstalling numpy-1.24.2:
      Successfully uninstalled numpy-1.24.2
Note: you may need to restart the kernel to use updated packages.


In [40]:
# Définir l'espace de recherche des hyperparamètres
param_space = {
    'learning_rate': (0.01, 0.6),
    'n_estimators': (50, 200),
    'max_depth': (3, 10),
    'min_child_weight': (1, 5),
    'gamma': (0.0, 1.0),
    'subsample': (0.5, 1.0),
    'colsample_bytree': (0.5, 1.0),
}

# Effectuer une recherche de paramètres en utilisant la recherche bayésienne
search = BayesSearchCV(
    model,
    param_space,
    n_iter=50,  # Nombre d'itérations de la recherche bayésienne
    scoring='roc_auc',  # Métrique à optimiser (vous pouvez choisir une autre métrique)
    cv=5,  # Nombre de plis de validation croisée
    n_jobs=-1  # Utiliser tous les cœurs disponibles
)

# Exécution de la recherche de paramètres
search.fit(X_train, y_train)

# Afficher les meilleurs paramètres et le score correspondant
print("Meilleurs paramètres:", search.best_params_)
print("Meilleur score:", search.best_score_)

# Évaluer le modèle avec les meilleurs paramètres sur l'ensemble de test
best_model = search.best_estimator_
y_pred = best_model.predict(X_test)
roc_auc2 = roc_auc_score(y_test, y_pred)
print("Précision sur l'ensemble de test avec les meilleurs paramètres:", roc_auc2)


AttributeError: module 'numpy' has no attribute 'int'.
`np.int` was a deprecated alias for the builtin `int`. To avoid this error in existing code, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
The aliases was originally deprecated in NumPy 1.20; for more details and guidance see the original release note at:
    https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations

Construire un modèle dédié afin de pouvoir prédir les perfomances en fonction des hyperparamètres utilisés.